
# Matrix Perturbation Correlation Comparison
This example demonstrates how to generate a matrix comparison plot for the perturbation correlation method (described in 
`sphx_glr_auto_examples_matrix_plot_matrix_of_perturbation_plots.py` and 
`sphx_glr_auto_examples_correlation_plot_perturbation_correlation_plot.py`). This example compares the calculated correlation
correlation coefficient to the TSUNAMI-IP calculated $c_k$ value for a set of dummy SDFs taken becuase they only use cross
sections available in the dummy 56 group library. **Note** before running this example, please ensure that the necessary cross section 
libraries are cached by running the `sphx_glr_auto_examples_correlation_plot_perturbation_correlation_plot.py` example.)


## Getting TSUNAMI-IP $c_k$ Values
First, we need to get the TSUNAMI-IP $c_k$ values for the experiment and application SDFs we want to compare. We can do this
by using the :func:`tsunami_ip_utils.integral_indices.get_integral_indices` function, as shown in 
`sphx_glr_auto_examples_integral_index_reader.py`.



In [ ]:
from tsunami_ip_utils.integral_indices import get_integral_indices
from paths import EXAMPLES

application_sdfs = [ EXAMPLES / 'data' / 'example_sdfs' / 'u235-dummy' / f'sphere_model_{i}.sdf' for i in range(1, 4) ]
experiment_sdfs = application_sdfs

# Get the TSUNAMI-IP integral indices
coverx_library = '56groupcov7.1'
integral_indices = get_integral_indices(application_sdfs, experiment_sdfs, coverx_library=coverx_library)
c_k = integral_indices['c_k']

## Generating the Comparison
A matrix comparison plot comparing the computed correlation coefficient to the TSUNAMI-IP $c_k$ values can be generated using
the :func:`tsunami_ip_utils.comparisons.correlation_comparison` function. Note this function is used to compare any method for computing
any of the available TSUNAMI-IP integral indices ($E$ and $c_k$). 



In [ ]:
from pathlib import Path
from tsunami_ip_utils.comparisons import correlation_comparison

# Define paths used for generating cross section perturbations
multigroup_library = EXAMPLES / 'data' / 'dummy_56_v7.1'
perturbation_factors = Path("~/codes/SCALE-6.3.1/data/perturb/56n.v7.1")

## 50 Points
First, we'll generate a comparison for 50 points



In [ ]:
num_perturbations = 50
comparisons, fig = correlation_comparison(
    integral_index_matrix=c_k,
    integral_index_name='c_k',
    application_files=application_sdfs, 
    experiment_files=experiment_sdfs, 
    method='perturbation',
    base_library=multigroup_library,
    perturbation_factors=perturbation_factors,
    num_perturbations=num_perturbations,
)

fig.show()
print(comparisons)

From this we can see an interactive matrix plot showing the perturbation correlation plots with the computed pearson and spearman
correlation coefficients and the TSUNAMI-IP computed $c_k$ values. Note that any plots disagreeing more than 5% are highlighted
in red. In addition, we get a multi-index pandas dataframe showing the comparisons (which can be written to excel as in
`sphx_glr_auto_examples_comparisons_compare_E.py`).
Note that all of the plot objects are generated using the defaults, and the matrix plot is also generated using the defaults.
If you want to customize the plot, just pass in ``plot_object_kwargs`` or ``matrix_plot_kwargs`` to the function.



## 200 Points
Now, using a slightly larger number of points: 200 (remember 1000 is the maximum), we can generate another comparison, but this time
using static matplotlib plots and including labels



In [ ]:
num_perturbations = 200
labels = {
    'applications': [ application_file.name for application_file in application_sdfs ],
    'experiments': [ experiment_file.name for experiment_file in experiment_sdfs ],
}
comparisons, fig = correlation_comparison(
    integral_index_matrix=c_k,
    integral_index_name='c_k',
    application_files=application_sdfs, 
    experiment_files=experiment_sdfs, 
    method='perturbation',
    base_library=multigroup_library,
    perturbation_factors=perturbation_factors,
    num_perturbations=num_perturbations,
    plot_objects_kwargs={'plot_type': 'scatter'},
    matrix_plot_kwargs={'labels': labels}
)

fig.show()
print(comparisons)

Note that for these examples, adding more poins hardly changes the agreement, because the TSUNAMI_IP $c_k$ values are ~1, only
a small number of points are needed to get a small uncertainty on the correlation coefficient (see `the technical manual <sec-pearson-coefficient>`
for details).



These plots can also be saved to an image



In [ ]:
comparisons, fig = correlation_comparison(
    integral_index_matrix=c_k,
    integral_index_name='c_k',
    application_files=application_sdfs, 
    experiment_files=experiment_sdfs, 
    method='perturbation',
    base_library=multigroup_library,
    perturbation_factors=perturbation_factors,
    num_perturbations=num_perturbations,
    plot_objects_kwargs={'plot_type': 'scatter'},
    matrix_plot_kwargs={'labels': labels}
)
fig.to_image( EXAMPLES / '_static' / 'perturbation_matrix_comparison.png' )

# sphinx_gallery_thumbnail_path = '../../examples/_static/perturbation_matrix_comparison.png'

## A Comparison Without a Plot
Sometimes generating the plots themselves can be extremely memory intensive when making a matrix plot comparison over an entire
series of critical experiments, so sometimes it is desirable to generate the comparison without the plot. This can be done by
passing ``make_plot=False`` to the :func:`tsunami_ip_utils.comparisons.correlation_comparison` function. This will return only
the comparisons dataframe.



In [ ]:
comparisons = correlation_comparison(
    integral_index_matrix=c_k,
    integral_index_name='c_k',
    application_files=application_sdfs, 
    experiment_files=experiment_sdfs, 
    method='perturbation',
    base_library=multigroup_library,
    perturbation_factors=perturbation_factors,
    num_perturbations=num_perturbations,
    make_plot=False,
)
print(comparisons)

Note also that, since generating points for perturbation plots can be time consuming, this function by default runs in parallel
with two less than the number of cores available on your machine. This can be changed by passing the ``num_cores`` argument.
